# Import

In [ ]:
import pandas as pd
from prophet import Prophet

# Init

# Playground

In [ ]:
df = pd.read_csv(
    "https://raw.githubusercontent.com/facebook/prophet/main/examples/example_wp_log_peyton_manning.csv"
)
df.head()

In [ ]:
m = Prophet()
m.fit(df)

In [ ]:
df.describe()

In [ ]:
df.tail()

In [ ]:
future = m.make_future_dataframe(periods=365)
future.tail()

In [ ]:
future.describe()

In [ ]:
forecast = m.predict(future)
forecast[["ds", "yhat", "yhat_lower", "yhat_upper"]].tail()

In [ ]:
fig1 = m.plot(forecast)

In [ ]:
fig2 = m.plot_components(forecast)

In [ ]:
from prophet.plot import plot_plotly, plot_components_plotly

plot_plotly(m, forecast)

In [ ]:
plot_components_plotly(m, forecast)

# Hands on

## Import

In [9]:
import os
import sys
import logging
import multiprocessing
import pandas as pd
import numpy as np
import sqlalchemy
import exchange_calendars as xcals
from dotenv import load_dotenv

# import exchange_calendars as xcals
from datetime import datetime, timedelta

# import pytz
# import pandas as pd
# from IPython.display import display, HTML
from sqlalchemy import create_engine
from sqlalchemy.dialects.postgresql import insert, TEXT
from concurrent.futures import ThreadPoolExecutor
from functools import lru_cache

from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly, add_changepoints_to_plot, plot_yearly, plot_seasonality_plotly

## Init

In [4]:
load_dotenv()  # take environment variables from .env.

module_path = os.getenv("LOCAL_AKSHARE_DEV_MODULE")
if module_path is not None and module_path not in sys.path:
    sys.path.insert(0, module_path)
import akshare as ak  # noqa: E402

print(ak.__version__)

DB_USER = os.getenv("DB_USER")
DB_PASSWORD = os.getenv("DB_PASSWORD")
DB_HOST = os.getenv("DB_HOST")
DB_PORT = os.getenv("DB_PORT")
DB_NAME = os.getenv("DB_NAME")

# Create an engine instance
alchemyEngine = create_engine(
    f"postgresql+psycopg2://{DB_USER}:{DB_PASSWORD}@{DB_HOST}:{DB_PORT}/{DB_NAME}",
    pool_recycle=3600,
)

logger = logging.getLogger(__name__)
logger.setLevel(logging.ERROR)

file_handler = logging.FileHandler("etl.log")
console_handler = logging.StreamHandler()

# Step 4: Create a formatter
formatter = logging.Formatter("%(name)s - %(levelname)s - %(message)s")

# Step 5: Attach the formatter to the handlers
file_handler.setFormatter(formatter)
console_handler.setFormatter(formatter)

# Step 6: Add the handlers to the logger
logger.addHandler(file_handler)
logger.addHandler(console_handler)

xshg = xcals.get_calendar("XSHG")

1.12.93


## Helper Functions

In [67]:
def predict(
    symbol, y_column, country=None, fourier_terms="auto", show_uncertainty=False
) -> (Prophet, pd.DataFrame, pd.DataFrame):  # type: ignore
    return predict_generic(
        "fund_etf_daily_em", symbol, y_column, country, fourier_terms, show_uncertainty
    )


def predict_generic(
    table, symbol, y_column, country=None, fourier_terms="auto", show_uncertainty=False,
) -> (Prophet, pd.DataFrame, pd.DataFrame):  # type: ignore
    query = f"SELECT * FROM {table} where symbol = '{symbol}' order by date"
    df = pd.read_sql(query, alchemyEngine, parse_dates=["date"])

    df = df.rename(
        columns={
            "date": "ds",
            y_column: "y",
        }
    )

    m = Prophet(
        mcmc_samples=300 if show_uncertainty else 0,
        daily_seasonality=False,
        weekly_seasonality=False,
        yearly_seasonality=fourier_terms,
    )  # Prophet object can only be fit once. Instantiate a new object.
    if country is not None:
        m.add_country_holidays(country_name=country)
    m.fit(df)

    future = m.make_future_dataframe(periods=60)
    forecast = m.predict(future)

    return (m, df, forecast)

## Asset 1: Bond

### Trial 1 - Bond IR Spread

#### load data from table

In [ ]:
# load all records from `bond_metrics_em` table into dataframe
query = "SELECT * FROM bond_metrics_em where china_yield_2y <> 'NaN'"
df = pd.read_sql(query, alchemyEngine, parse_dates=["date"])

# Display the first few rows of the dataframe
df.head()

In [ ]:
df.describe()

#### transform DF to Prophet schema

In [ ]:
df = df.rename(columns={
    "date": "ds",
    "china_yield_spread_10y_2y": "y",
})

#### fitting

In [ ]:
m = Prophet()
m.fit(df)

#### predicting

In [ ]:
future = m.make_future_dataframe(periods=365)
forecast = m.predict(future)
forecast[["ds", "yhat", "yhat_lower", "yhat_upper"]].tail()

#### plotting

In [ ]:
fig1 = m.plot(forecast)

In [ ]:
fig2 = m.plot_components(forecast)

In [ ]:
plot_plotly(m, forecast)

In [ ]:
plot_components_plotly(m, forecast)

### 城投债ETF 511220

In [ ]:
symbol = "511220"
m, df, forecast = predict(symbol, "close")
df.describe()

In [ ]:
plot_plotly(m, forecast)

In [ ]:
symbol = "511220"
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

### 30年国债ETF 511090

In [ ]:
symbol = "511090"
m, df, forecast = predict(symbol, 'close')

In [ ]:
fig1 = m.plot(forecast)

In [ ]:
fig2 = m.plot_components(forecast)

## Asset 2: Domestic Stock

### 创业板50ETF 159949

In [24]:
symbol = "159949"
m, df, forecast = predict(symbol, "close")
df.describe()

16:04:27 - cmdstanpy - INFO - Chain [1] start processing
16:04:28 - cmdstanpy - INFO - Chain [1] done processing


ds         open            y         high  \
count                           1861  1861.000000  1861.000000  1861.000000   
mean   2020-05-19 17:01:23.181085440     0.891608     0.891960     0.901956   
min              2016-07-22 00:00:00     0.421000     0.425000     0.433000   
25%              2018-06-21 00:00:00     0.681000     0.682000     0.688000   
50%              2020-05-21 00:00:00     0.826000     0.825000     0.836000   
75%              2022-04-20 00:00:00     1.088000     1.085000     1.100000   
max              2024-03-20 00:00:00     1.593000     1.585000     1.597000   
std                              NaN     0.286705     0.286962     0.290497   

               low        volume      turnover    amplitude  change_rate  \
count  1861.000000  1.861000e+03  1.861000e+03  1861.000000  1861.000000   
mean      0.881466  6.472235e+06  5.831699e+08     2.266405     0.004981   
min       0.419000  7.441000e+03  6.782780e+05     0.000000    -8.160000   
25%       0.673000  3.463001e+06  2.325545e+08     1.450000    -1.000000   
50%       0.818000  6.212869e+06  5.346874e+08     2.010000    -0.110000   
75%       1.070000  8.712688e+06  8.378951e+08     2.780000     0.990000   
max       1.565000  3.391140e+07  2.975649e+09     8.240000     8.330000   
std       0.282627  4.978680e+06  4.787844e+08     1.151445     1.774682   

       change_amount  turnover_rate  
count    1861.000000    1861.000000  
mean       -0.000095       2.796072  
min        -0.074000       0.000000  
25%        -0.008000       1.500000  
50%        -0.001000       2.680000  
75%         0.008000       3.760000  
max         0.089000      14.650000  
std         0.016629       2.150701

In [ ]:
plot_plotly(m, forecast)

In [25]:
symbol = "159949"
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

16:04:33 - cmdstanpy - INFO - Chain [1] start processing
16:04:33 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



### 红利低波50ETF 515450

In [55]:
symbol = "515450"
m, df, forecast = predict(symbol, "close")
df.describe()

14:35:35 - cmdstanpy - INFO - Chain [1] start processing
14:35:35 - cmdstanpy - INFO - Chain [1] done processing


ds        open           y        high  \
count                            989  989.000000  989.000000  989.000000   
mean   2022-03-07 16:47:33.791708672    0.996893    0.997828    1.004843   
min              2020-02-26 00:00:00    0.668000    0.661000    0.670000   
25%              2021-03-03 00:00:00    0.898000    0.898000    0.910000   
50%              2022-03-09 00:00:00    0.988000    0.991000    0.998000   
75%              2023-03-15 00:00:00    1.119000    1.113000    1.127000   
max              2024-03-21 00:00:00    1.334000    1.334000    1.339000   
std                              NaN    0.165180    0.164563    0.165224   

              low        volume      turnover   amplitude  change_rate  \
count  989.000000  9.890000e+02  9.890000e+02  989.000000   989.000000   
mean     0.989388  1.928766e+05  2.363075e+07    1.565379     0.062770   
min      0.638000  1.970000e+03  2.048670e+05    0.000000    -5.800000   
25%      0.889000  1.096450e+05  1.128754e+07    0.950000    -0.590000   
50%      0.982000  1.990990e+05  2.422228e+07    1.320000     0.000000   
75%      1.108000  2.421900e+05  2.996547e+07    1.950000     0.690000   
max      1.324000  2.181967e+06  2.867586e+08   12.930000     9.070000   
std      0.163938  1.533846e+05  1.990339e+07    1.015588     1.149966   

       change_amount  turnover_rate  
count     989.000000     989.000000  
mean        0.000559       1.523782  
min        -0.057000       0.020000  
25%        -0.006000       0.870000  
50%         0.000000       1.570000  
75%         0.007000       1.910000  
max         0.067000      17.240000  
std         0.011118       1.211755

In [ ]:
plot_plotly(m, forecast)

In [57]:
m, df, forecast = predict(symbol, "change_rate")
plot_seasonality_plotly(m=m, name="yearly", figsize=(1200, 400))

14:35:42 - cmdstanpy - INFO - Chain [1] start processing
14:35:42 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



In [59]:
# plot_components_plotly(m, forecast)
m, df, forecast = predict(symbol, "change_rate", country="China")
plot_components_plotly(m, forecast)
# plot_seasonality_plotly(m=m, name="yearly", figsize=(1200, 400))

14:37:21 - cmdstanpy - INFO - Chain [1] start processing
14:37:21 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



### 红利低波100ETF 515100

In [64]:
symbol = "515100"
m, df, forecast = predict(symbol, "close")
df.describe()

15:07:08 - cmdstanpy - INFO - Chain [1] start processing
15:07:08 - cmdstanpy - INFO - Chain [1] done processing


ds        open           y        high  \
count                            903  903.000000  903.000000  903.000000   
mean   2022-05-11 06:54:37.076412160    1.054542    1.055701    1.064238   
min              2020-07-03 00:00:00    0.613000    0.628000    0.633000   
25%              2021-06-07 12:00:00    0.899000    0.899000    0.902500   
50%              2022-05-16 00:00:00    1.072000    1.074000    1.082000   
75%              2023-04-15 12:00:00    1.244000    1.248500    1.258500   
max              2024-03-21 00:00:00    1.492000    1.424000    1.492000   
std                              NaN    0.202689    0.202473    0.203221   

              low        volume      turnover   amplitude  change_rate  \
count  903.000000  9.030000e+02  9.030000e+02  903.000000   903.000000   
mean     1.045427  2.392345e+05  3.564200e+07    1.820465     0.092414   
min      0.611000  1.033000e+03  1.367810e+05    0.000000    -6.770000   
25%      0.892000  5.290300e+04  7.165158e+06    1.030000    -0.655000   
50%      1.061000  1.036760e+05  1.563776e+07    1.490000     0.080000   
75%      1.235000  1.803455e+05  2.998726e+07    2.180000     0.840000   
max      1.417000  7.219443e+06  1.277551e+09   17.300000    11.620000   
std      0.201598  5.362581e+05  7.789826e+07    1.309892     1.374552   

       change_amount  turnover_rate  
count     903.000000     903.000000  
mean        0.000775       0.406456  
min        -0.071000       0.000000  
25%        -0.007000       0.090000  
50%         0.001000       0.180000  
75%         0.009000       0.310000  
max         0.073000      12.260000  
std         0.013800       0.910941

In [66]:
plot_plotly(m, forecast)

In [72]:
m, df, forecast = predict(symbol, "change_rate")
# plot_components_plotly(m, forecast)
plot_seasonality_plotly(m=m, name="yearly", figsize=(1200, 400))

15:40:05 - cmdstanpy - INFO - Chain [1] start processing
15:40:06 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



In [63]:
m.predictive_samples(forecast)

{'yhat': array([[-1.08124982,  1.97425926, -1.53258396, ..., -0.66323002,
         -0.27958538, -0.70408459],
        [-0.11281361,  0.91233374, -1.4380186 , ...,  2.47297916,
          1.52300092, -1.31011048],
        [-0.26646794, -0.28598582,  1.46756901, ...,  0.05435485,
          1.07694203, -1.29112494],
        ...,
        [ 0.52317967,  0.17323515, -1.019786  , ...,  0.26777646,
          0.22233547, -0.82121041],
        [-1.69749103,  0.70971775, -0.39084396, ...,  0.16902329,
         -0.64672575, -2.60523686],
        [-0.38206605,  2.42074589,  1.06285294, ..., -0.91935853,
          1.34139383,  0.43104029]]),
 'trend': array([[0.06567161, 0.06567161, 0.06567161, ..., 0.06567161, 0.06567161,
         0.06567161],
        [0.06568251, 0.06568251, 0.06568251, ..., 0.06568251, 0.06568251,
         0.06568251],
        [0.06569342, 0.06569342, 0.06569342, ..., 0.06569342, 0.06569342,
         0.06569342],
        ...,
        [0.05341867, 0.05284802, 0.05140736, ..., 0.053

## Asset 3: Commodities

### 黄金ETF 518880

In [ ]:
symbol = "518880"
m, df, forecast = predict(symbol, "close")
df.describe()

In [ ]:
plot_plotly(m, forecast)

In [ ]:
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

### 大宗商品ETF 510170

In [26]:
symbol = "510170"
m, df, forecast = predict(symbol, "close")
df.describe()

16:33:41 - cmdstanpy - INFO - Chain [1] start processing
16:33:43 - cmdstanpy - INFO - Chain [1] done processing


ds         open            y         high  \
count                           3155  3155.000000  3155.000000  3155.000000   
mean   2017-08-19 18:43:42.123613184     0.570132     0.571073     0.577366   
min              2011-01-25 00:00:00     0.313000     0.313000     0.316000   
25%              2014-05-02 12:00:00     0.415000     0.416000     0.420000   
50%              2017-08-08 00:00:00     0.513000     0.513000     0.519000   
75%              2020-12-15 12:00:00     0.737000     0.740000     0.748000   
max              2024-03-20 00:00:00     1.144000     1.137000     1.150000   
std                              NaN     0.184063     0.183740     0.186012   

               low        volume      turnover    amplitude  change_rate  \
count  3155.000000  3.155000e+03  3.155000e+03  3155.000000  3155.000000   
mean      0.563185  8.390943e+04  2.061753e+07     2.472891     0.023363   
min       0.303000  1.000000e+00  8.900000e+01     0.000000   -10.020000   
25%       0.410000  5.045000e+02  8.670350e+04     1.300000    -0.875000   
50%       0.505000  1.293900e+04  1.549674e+06     1.950000     0.000000   
75%       0.725500  5.119400e+04  1.116644e+07     2.995000     0.970000   
max       1.086000  2.203136e+06  7.049915e+08    20.050000    10.060000   
std       0.181456  1.950592e+05  5.291309e+07     1.986223     1.803453   

       change_amount  turnover_rate  
count    3155.000000    3155.000000  
mean        0.000055       3.832897  
min        -0.061000       0.000000  
25%        -0.005000       0.020000  
50%         0.000000       0.590000  
75%         0.005000       2.340000  
max         0.062000     100.640000  
std         0.010571       8.910345

In [ ]:
plot_plotly(m, forecast)

In [27]:
symbol = "510170"
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

16:33:47 - cmdstanpy - INFO - Chain [1] start processing
16:33:47 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



### 能源ETF 159930

In [33]:
symbol = "159930"
m, df, forecast = predict(symbol, "close")
df.describe()

11:35:32 - cmdstanpy - INFO - Chain [1] start processing
11:35:36 - cmdstanpy - INFO - Chain [1] done processing


ds         open            y         high  \
count                           2552  2552.000000  2552.000000  2552.000000   
mean   2018-12-18 19:11:39.686520320     0.889199     0.890771     0.900466   
min              2013-09-16 00:00:00     0.555000     0.557000     0.562000   
25%              2016-05-05 18:00:00     0.741750     0.741000     0.748750   
50%              2018-12-15 12:00:00     0.831000     0.834000     0.839000   
75%              2021-08-02 06:00:00     1.029250     1.030000     1.055000   
max              2024-03-21 00:00:00     1.585000     1.586000     1.610000   
std                              NaN     0.206813     0.207911     0.211576   

               low        volume      turnover    amplitude  change_rate  \
count  2552.000000  2.552000e+03  2.552000e+03  2552.000000  2552.000000   
mean      0.878850  8.777616e+04  8.576586e+06     2.333182     0.031634   
min       0.554000  2.600000e+01  2.082000e+03     0.000000   -10.040000   
25%       0.731000  2.266750e+03  1.800672e+05     1.287500    -0.780000   
50%       0.825000  1.184500e+04  1.111699e+06     1.880000     0.000000   
75%       1.015000  1.448485e+05  1.349355e+07     2.820000     0.832500   
max       1.560000  1.217108e+06  1.152649e+08    15.100000    10.050000   
std       0.202621  1.375573e+05  1.372846e+07     1.656014     1.803943   

       change_amount  turnover_rate  
count    2552.000000    2552.000000  
mean        0.000184       4.074397  
min        -0.123000       0.000000  
25%        -0.006000       0.110000  
50%         0.000000       0.550000  
75%         0.007000       6.722500  
max         0.140000      56.510000  
std         0.018188       6.385931

In [ ]:
plot_plotly(m, forecast)

In [34]:
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

11:35:48 - cmdstanpy - INFO - Chain [1] start processing
11:35:48 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



### 能源化工ETF 159981

In [ ]:
symbol = "159981"
m, df, forecast = predict(symbol, "close")
df.describe()

In [ ]:
plot_plotly(m, forecast)

In [ ]:
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

### 豆粕 159985

In [ ]:
symbol = "159985"
m, df, forecast = predict(symbol, "close")
df.describe()

In [ ]:
plot_plotly(m, forecast)

In [ ]:
m, df, forecast = predict(symbol, "change_rate")
plot_components_plotly(m, forecast)

## Asset 4: Overseas

### 纳斯达克100 513110

In [31]:
symbol = ".IXIC"
table = "us_index_daily_sina_view"
# we need to use the US index instead of ETF daily historical data per se, due to insufficient ETF market data
m, df, forecast = predict_generic(table, symbol, "close", "US")
df.describe()

11:34:40 - cmdstanpy - INFO - Chain [1] start processing
11:34:44 - cmdstanpy - INFO - Chain [1] done processing


ds          open             y  \
count                           5088   5088.000000   5088.000000   
mean   2014-02-08 18:22:21.509433856   5613.730949   5614.671122   
min              2004-01-02 00:00:00   1284.840000   1268.640000   
25%              2009-01-21 18:00:00   2360.060050   2357.589925   
50%              2014-02-10 12:00:00   4125.140150   4124.855000   
75%              2019-03-01 18:00:00   7786.735075   7789.517700   
max              2024-03-20 00:00:00  16322.102500  16369.407200   
std                              NaN   4091.338472   4092.032612   

               high           low        volume        amount  change_rate  
count   5088.000000   5088.000000  5.088000e+03  5.088000e+03  5088.000000  
mean    5651.063958   5572.874138  2.393875e+09  9.173193e+12     0.050438  
min     1316.150000   1265.520000  0.000000e+00  0.000000e+00   -12.310000  
25%     2375.314975   2339.262400  1.745037e+09  3.791630e+12    -0.540000  
50%     4139.059800   4094.000000  1.982650e+09  5.395955e+12     0.100000  
75%     7831.752700   7725.339850  2.526040e+09  9.742958e+12     0.720000  
max    16449.703100  16199.056600  1.021339e+10  1.431070e+14    11.810000  
std     4120.846556   4058.706384  1.080992e+09  1.302889e+13     1.352683

In [ ]:
plot_plotly(m, forecast)

In [32]:
m, df, forecast = predict_generic(table, symbol, "change_rate", "US")
plot_components_plotly(m, forecast)

11:34:54 - cmdstanpy - INFO - Chain [1] start processing
11:34:55 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



### 标普500ETF 513500

In [ ]:
symbol = "513500"
m, df, forecast = predict(symbol, "close", "US")
df.describe()

In [ ]:
plot_plotly(m, forecast)

In [ ]:
symbol = "513500"
m, df, forecast = predict(symbol, "change_rate", "US")
plot_components_plotly(m, forecast)

### 日本东证指数ETF 513800

In [35]:
symbol = "513800"
m, df, forecast = predict(symbol, "close", "JP")
df.describe()

13:24:31 - cmdstanpy - INFO - Chain [1] start processing
13:24:32 - cmdstanpy - INFO - Chain [1] done processing


ds         open            y         high  \
count                           1152  1152.000000  1152.000000  1152.000000   
mean   2021-11-04 22:36:14.999999744     1.115888     1.116035     1.124478   
min              2019-06-25 00:00:00     0.848000     0.829000     0.850000   
25%              2020-08-26 18:00:00     1.044750     1.044000     1.054000   
50%              2021-11-06 12:00:00     1.106000     1.106000     1.112000   
75%              2023-01-10 06:00:00     1.179000     1.179000     1.186000   
max              2024-03-21 00:00:00     1.435000     1.448000     1.463000   
std                              NaN     0.101342     0.101226     0.101543   

               low        volume      turnover    amplitude  change_rate  \
count  1152.000000  1.152000e+03  1.152000e+03  1152.000000  1152.000000   
mean      1.108057  2.534149e+04  3.274298e+06     1.486997     0.038802   
min       0.825000  2.000000e+00  2.290000e+02     0.000000    -5.340000   
25%       1.034000  3.310000e+02  3.723500e+04     0.650000    -0.510000   
50%       1.097500  1.463500e+03  1.534220e+05     1.060000     0.080000   
75%       1.173000  9.266250e+03  9.894905e+05     1.730000     0.600000   
max       1.435000  1.922658e+06  2.575840e+08    13.770000     4.870000   
std       0.101535  1.164338e+05  1.573406e+07     1.545230     1.050800   

       change_amount  turnover_rate  
count    1152.000000    1152.000000  
mean        0.000401       0.477335  
min        -0.056000       0.000000  
25%        -0.006000       0.010000  
50%         0.001000       0.030000  
75%         0.007000       0.172500  
max         0.054000      36.230000  
std         0.011453       2.193610

In [ ]:
plot_plotly(m, forecast)

In [36]:
m, df, forecast = predict(symbol, "change_rate", "JP")
plot_components_plotly(m, forecast)

13:24:42 - cmdstanpy - INFO - Chain [1] start processing
13:24:42 - cmdstanpy - INFO - Chain [1] done processing
/Users/jx/.pyenv/versions/3.12.2/envs/venv_3.12.2/lib/python3.12/site-packages/plotly/io/_json.py:560: UserWarning:

Discarding nonzero nanoseconds in conversion.



# Output top-N TS component graph with highest Sortino Ratio

In [ ]:
top_n = 100
since_inception = "6 months"
query = f"""
    SELECT fundcode, fundname, sortinoratio sortino 
    FROM fund_etf_perf_em 
    where 
        sortinoratio is not null 
        and sortinoratio <> 'nan'
        and inceptiondate <= CURRENT_DATE - interval '{since_inception}'
    order by sortinoratio desc limit {top_n}
"""
df = pd.read_sql(query, alchemyEngine)

# Ensure the directory for saving images exists
output_dir = '/Users/jx/Downloads/ETF_forecast'
os.makedirs(output_dir, exist_ok=True)

for index, row in df.iterrows():
    fundcode = row['fundcode']
    fundname = row['fundname'].replace(' ', '_')  # Replace spaces with underscores for filename
    sortino = row['sortino']
    timestamp = datetime.now().strftime('%Y%m%d%H%M%S')

    # Predict and forecast 'close'
    m, df, forecast = predict(fundcode, 'close')
    fig1 = m.plot(forecast)
    fig1.savefig(f'{output_dir}/{fundcode}_{fundname}_{sortino}_forecast_{timestamp}.png')

    # Predict and forecast 'change_rate'
    m, df, forecast = predict(fundcode, 'change_rate')
    fig2 = m.plot_components(forecast)
    fig2.savefig(f'{output_dir}/{fundcode}_{fundname}_{sortino}_components_{timestamp}.png')